In [20]:
import pandas as pd
import re
import json
import os

In [21]:
# 设置最大文件大小限制为100MB
max_file_size = 100 * 1024 * 1024  # 100MB in bytes

In [22]:
model = "glm-4-air"

In [23]:
# 定义字典模板
request_template = {
    "custom_id": "",
    "method": "POST",
    "url": "/v4/chat/completions",
    "body": {
        "model": model,
        "messages": [
            {"role": "user", "content": ""}
        ],
        "temperature": 0.1
    }
}

content_template = \
"""
    ## Role
        -你是一个关系抽取专家.
    ## Goals
        -首先判断给定的金融新闻文本中是否存在企业间的关联关系，并仅在存在关联关系的情况下进行关系提取。
    ## Constrains
        -必须提取以下类型的关系：投资、收购、合作、供应商、技术转让。
        -输出结果必须为三元组格式，不能包含其他多余的提示信息。
    ## Output
        -如果存在关联关系，输出格式：(企业A, 投资, 企业B)；(企业C, 收购, 企业D)；(企业E, 供应商, 企业F) 
        -如果不存在关联关系，输出：“无关联关系”。
    ## Workflow
        1. 读取并理解给定的文本内容:{}
        2. 判断文本中是否存在企业间的关联关系。
        3. 如果存在关联关系，则以三元组形式输出提取的关系。
        4. 如果不存在关联关系，则输出：“无关联关系”。
"""

In [26]:
# 年份
year = '2024'
news_file = f'./news/df_{year}.csv'
request_save_path = f'./news/request/{model}'
os.makedirs(request_save_path, exist_ok=True)

In [27]:
# 初始化文件编号
request_file_number = 1
# 文件名
request_file_name = f"{year}_request-{request_file_number}.jsonl"
# 文件路径
request_file_path = os.path.join(request_save_path, request_file_name)

# 文件内的单个请求 id
# request_id = 1
# 字典保存每一天新闻对应的request
request_id_2_location= {}

df = pd.read_csv(news_file)
for request_id, news in enumerate(df['正文'], start=1):
    # print(news)
    request_data = request_template.copy()
    # 更新 request-id 和新闻内容
    request_data["custom_id"] = f"request-{request_id}"

    # 整个表达式的结果是删除 content_template.format(news) 中的所有空白字符
    content = re.sub(r"\s+", "", content_template.format(news))
    # 填入请求
    request_data["body"]["messages"][0]["content"] = content
    # 序列化为 JSON 字符串并写入文件
    json_line = json.dumps(request_data, ensure_ascii=False)
    json_line_size = len(json_line.encode('utf-8'))

    # 检查文件大小，如果超过最大限制则更换文件名
    if os.path.exists(request_file_path) and os.path.getsize(request_file_path) + json_line_size >= max_file_size:
        request_file_number += 1
        request_file_name = f"{year}_request-{request_file_number}.jsonl"
        request_file_path = os.path.join(request_save_path, request_file_name)
        # 记录当前新闻对应的request_id和文件名
        request_id_2_location[request_id] = request_file_number
    
    # 写入文件
    with open(request_file_path, 'a', encoding='utf-8') as file:
        print(f"第{request_id}条新闻写入文件{request_file_name}")
        file.write(json_line + '\n')
    # 加1
    request_id += 1

# 将字典转换为JSON字符串并保存到文件
with open(f"request_id_2_location_{year}.json", 'w', encoding='utf-8') as mapping_file:
    json.dump(request_id_2_location, mapping_file, ensure_ascii=False, indent=4)

第1条新闻写入文件2024_request-1.jsonl
第2条新闻写入文件2024_request-1.jsonl
第3条新闻写入文件2024_request-1.jsonl
第4条新闻写入文件2024_request-1.jsonl
第5条新闻写入文件2024_request-1.jsonl
第6条新闻写入文件2024_request-1.jsonl
第7条新闻写入文件2024_request-1.jsonl
第8条新闻写入文件2024_request-1.jsonl
第9条新闻写入文件2024_request-1.jsonl
第10条新闻写入文件2024_request-1.jsonl
第11条新闻写入文件2024_request-1.jsonl
第12条新闻写入文件2024_request-1.jsonl
第13条新闻写入文件2024_request-1.jsonl
第14条新闻写入文件2024_request-1.jsonl
第15条新闻写入文件2024_request-1.jsonl
第16条新闻写入文件2024_request-1.jsonl
第17条新闻写入文件2024_request-1.jsonl
第18条新闻写入文件2024_request-1.jsonl
第19条新闻写入文件2024_request-1.jsonl
第20条新闻写入文件2024_request-1.jsonl
第21条新闻写入文件2024_request-1.jsonl
第22条新闻写入文件2024_request-1.jsonl
第23条新闻写入文件2024_request-1.jsonl
第24条新闻写入文件2024_request-1.jsonl
第25条新闻写入文件2024_request-1.jsonl
第26条新闻写入文件2024_request-1.jsonl
第27条新闻写入文件2024_request-1.jsonl
第28条新闻写入文件2024_request-1.jsonl
第29条新闻写入文件2024_request-1.jsonl
第30条新闻写入文件2024_request-1.jsonl
第31条新闻写入文件2024_request-1.jsonl
第32条新闻写入文件2024_request-1.jsonl
第33条新闻写入文件2024_re